In [1]:
# !pip install datapungibea
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopandas
import os

In [2]:
#import data and convert datatype to int64
data = pd.read_csv('AbiData.csv')
# data.astype('int64')
# data = data.apply(pd.to_numeric, errors='coerce')
for column in data.columns:
    if data[column].dtype == 'object':
        data[column] = pd.to_numeric(data[column].str.replace(',', ''), errors='coerce').astype('Int64')
        


In [4]:
#set index as GeoFips and TimePeriod
data = data.set_index(["GeoFips", "TimePeriod"])

In [6]:
#let dataframe be equal to data imported
full_df = data

#convert dataframe to float64
full_df = full_df.astype('float64')

Download interest rate data (divisia), and average it annually

In [10]:
divisia = pd.read_excel("https://centerforfinancialstability.org/amfm/Divisia.xlsx", 
                        sheet_name = "Broad", header  =1, index_col = "Date")

index = divisia.index
keys = divisia.keys()
divisia = divisia.resample("A").mean().rename(columns={keys[0]: "M4",
                                                       keys[2]:"M4 Interest Rate"})
year_lst = [i for i in range(1966, 2024)]
divisia = divisia[["M4", "M4 Interest Rate"]].reset_index()
divisia["TimePeriod"] = year_lst
divisia = divisia.set_index("TimePeriod").drop(columns = "Date")
divisia.head()

M4  M4 Interest Rate
TimePeriod                              
1966        103.843982          0.033092
1967        111.124365          0.036325
1968        116.666830          0.042463
1969        119.171882          0.042730
1970        130.436104          0.034850

Import inflation data

In [11]:
cpi = pd.read_csv('Annual_CPI_urban.csv')

In [12]:
cpi['DATE'] = pd.to_datetime(cpi['DATE'])

In [13]:
cpi['TimePeriod'] = cpi['DATE'].dt.year

In [14]:
cpi.drop('DATE', axis=1, inplace=True)

In [15]:
cpi['CPIAUCSL_PCA']=pd.to_numeric(cpi['CPIAUCSL_PCA'], errors='coerce')

In [16]:
cpi['inflation'] = cpi['CPIAUCSL_PCA'].pct_change()

In [17]:
cpi = cpi.set_index('TimePeriod')

In [20]:
divisia1 = divisia.copy()
divisia1 = divisia1.join(cpi).reset_index()
divisia1 = divisia1.set_index(['TimePeriod'])
divisia1 = divisia1.sort_index()
divisia1.head(50)

M4  M4 Interest Rate  CPIAUCSL_PCA  inflation
TimePeriod                                                        
1966         103.843982          0.033092           NaN        NaN
1967         111.124365          0.036325           NaN        NaN
1968         116.666830          0.042463           NaN        NaN
1969         119.171882          0.042730           NaN        NaN
1970         130.436104          0.034850           NaN        NaN
1971         144.401865          0.034712           NaN        NaN
1972         157.321435          0.050436           NaN        NaN
1973         166.896644          0.058927           NaN        NaN
1974         180.343641          0.045520           NaN        NaN
1975         198.899670          0.040336           NaN        NaN
1976         218.014139          0.042364           NaN        NaN
1977         234.421851          0.056209           NaN        NaN
1978         241.976193          0.075615           NaN        NaN
1979         247.104106          0.088508           NaN        NaN
1980         254.363897          0.112961           NaN        NaN
1981         267.941105          0.094079           NaN        NaN
1982         284.056268          0.074364           NaN        NaN
1983         300.143561          0.084334           NaN        NaN
1984         322.572117          0.067561           NaN        NaN
1985         353.593878          0.055376           NaN        NaN
1986         379.764735          0.054402           NaN        NaN
1987         397.353439          0.060903           NaN        NaN
1988         408.118752          0.071729           NaN        NaN
1989         426.896015          0.065818           NaN        NaN
1990         445.575551          0.049653           NaN        NaN
1991         468.277307          0.030239           NaN        NaN
1992         487.281823          0.024376           NaN        NaN
1993         503.616563          0.030563           NaN        NaN
1994         516.264776          0.040663           NaN        NaN
1995         544.844618          0.037547           NaN        NaN
1996         578.667036          0.038991           NaN        NaN
1997         624.629859          0.038022           NaN        NaN
1998         675.042845          0.035890           NaN        NaN
1999         716.138833          0.044508           NaN        NaN
2000         777.366744          0.027522           NaN        NaN
2001         842.493362          0.012311       2.81663        NaN
2002         890.722833          0.007415       1.59567  -0.433483
2003         935.225534          0.008946       2.29800   0.440147
2004         987.417840          0.020890       2.66757   0.160822
2005        1044.582478          0.032386       3.36583   0.261759
2006        1113.070987          0.033668       3.22209  -0.042706
2007        1203.409143          0.016335       2.87055  -0.109103
2008        1226.658697          0.003480       3.81495   0.328996
2009        1169.400546          0.001692      -0.32036  -1.083975
2010        1185.574288          0.001039       1.63657  -6.108534
2011        1223.671712          0.000960       3.13965   0.918433
2012        1274.150327          0.000731       2.07319  -0.339675
2013        1299.979150          0.000634       1.46597  -0.292892
2014        1342.896960          0.000651       1.61546   0.101973
2015        1409.131496          0.001404       0.12114  -0.925012

In [21]:
divisia['RM4Interest Rate'] = divisia1['M4 Interest Rate']-divisia1['inflation']

In [23]:
divisia['RM4'] = divisia1['M4'] / divisia1['CPIAUCSL_PCA']

In [25]:
divisia.head(40)

M4  M4 Interest Rate  RM4Interest Rate         RM4
TimePeriod                                                             
1966         103.843982          0.033092               NaN         NaN
1967         111.124365          0.036325               NaN         NaN
1968         116.666830          0.042463               NaN         NaN
1969         119.171882          0.042730               NaN         NaN
1970         130.436104          0.034850               NaN         NaN
1971         144.401865          0.034712               NaN         NaN
1972         157.321435          0.050436               NaN         NaN
1973         166.896644          0.058927               NaN         NaN
1974         180.343641          0.045520               NaN         NaN
1975         198.899670          0.040336               NaN         NaN
1976         218.014139          0.042364               NaN         NaN
1977         234.421851          0.056209               NaN         NaN
1978         241.976193          0.075615               NaN         NaN
1979         247.104106          0.088508               NaN         NaN
1980         254.363897          0.112961               NaN         NaN
1981         267.941105          0.094079               NaN         NaN
1982         284.056268          0.074364               NaN         NaN
1983         300.143561          0.084334               NaN         NaN
1984         322.572117          0.067561               NaN         NaN
1985         353.593878          0.055376               NaN         NaN
1986         379.764735          0.054402               NaN         NaN
1987         397.353439          0.060903               NaN         NaN
1988         408.118752          0.071729               NaN         NaN
1989         426.896015          0.065818               NaN         NaN
1990         445.575551          0.049653               NaN         NaN
1991         468.277307          0.030239               NaN         NaN
1992         487.281823          0.024376               NaN         NaN
1993         503.616563          0.030563               NaN         NaN
1994         516.264776          0.040663               NaN         NaN
1995         544.844618          0.037547               NaN         NaN
1996         578.667036          0.038991               NaN         NaN
1997         624.629859          0.038022               NaN         NaN
1998         675.042845          0.035890               NaN         NaN
1999         716.138833          0.044508               NaN         NaN
2000         777.366744          0.027522               NaN         NaN
2001         842.493362          0.012311               NaN  299.113963
2002         890.722833          0.007415          0.440898  558.212433
2003         935.225534          0.008946         -0.431201  406.973688
2004         987.417840          0.020890         -0.139933  370.156299
2005        1044.582478          0.032386         -0.229373  310.349150

Add/join the interest rates to the original dataframe

In [53]:
all_data = full_df.copy().reset_index().set_index("TimePeriod")
all_data = all_data.join(divisia).reset_index()     
all_data = all_data.set_index(["GeoFips", "TimePeriod"])    
all_data = all_data.sort_index()
all_data 

Accommodation and food services  \
GeoFips TimePeriod                                    
1001    2001                                46510.0   
        2002                                45576.0   
        2003                                48870.0   
        2004                                49738.0   
        2005                                46414.0   
...                                             ...   
56045   2016                                 3499.0   
        2017                                    NaN   
        2018                                    NaN   
        2019                                    NaN   
        2020                                    NaN   

                    Administrative and support and waste management and remediation services  \
GeoFips TimePeriod                                                                             
1001    2001                                                      NaN                          
        2002                                                      NaN                          
        2003                                                      NaN                          
        2004                                                      NaN                          
        2005                                                      NaN                          
...                                                               ...                          
56045   2016                                                    655.0                          
        2017                                                      NaN                          
        2018                                                      NaN                          
        2019                                                    756.0                          
        2020                                                    908.0                          

                    Agriculture, forestry, fishing and hunting  \
GeoFips TimePeriod                                               
1001    2001                                           22455.0   
        2002                                           18063.0   
        2003                                           39941.0   
        2004                                           49903.0   
        2005                                           59099.0   
...                                                        ...   
56045   2016                                           13871.0   
        2017                                           19901.0   
        2018                                           23787.0   
        2019                                           14194.0   
        2020                                            8653.0   

                    All industry total  Arts, entertainment, and recreation  \
GeoFips TimePeriod                                                            
1001    2001                  949800.0                               2150.0   
        2002                  984039.0                               1935.0   
        2003                 1008032.0                               1846.0   
        2004                 1170278.0                               1897.0   
        2005                 1195319.0                               2277.0   
...                                ...                                  ...   
56045   2016                  305446.0                                351.0   
        2017                  300909.0                                  NaN   
        2018                  315332.0                                  NaN   
        2019                  322576.0                                  NaN   
        2020                  312665.0                                  NaN   

                    Arts, entertainment, recreation, accommodation, and food services  \
GeoFips TimePeriod                                                             

In [29]:
def import_geo_data(filename, index_col = "Date", FIPS_name = "FIPS"):
    # import county level shapefile
    map_data = geopandas.read_file(filename = filename,                                   
                                   index_col = index_col)
    # rename fips code to match variable name in COVID-19 data
    map_data.rename(columns={"State":"state"},
                    inplace = True)
    # Combine statefips and county fips to create a single fips value
    # that identifies each particular county without referencing the 
    # state separately
    map_data[FIPS_name] = map_data["STATEFP"].astype(str) + \
        map_data["COUNTYFP"].astype(str)
    map_data[FIPS_name] = map_data[FIPS_name].astype(np.int64)
    # set FIPS as index
    map_data.set_index(FIPS_name, inplace=True)
    
    return map_data
fips_name = "fips_code"
map_data = import_geo_data(
    filename = "countiesWithStatesAndPopulation.shp",
    index_col = "Date", FIPS_name= fips_name)
map_data.head()

STATEFP COUNTYFP  COUNTYNS        AFFGEOID     NAME LSAD  \
fips_code                                                             
21007           21      007  00516850  0500000US21007  Ballard   06   
21017           21      017  00516855  0500000US21017  Bourbon   06   
21031           21      031  00516862  0500000US21031   Butler   06   
21065           21      065  00516879  0500000US21065   Estill   06   
21069           21      069  00516881  0500000US21069  Fleming   06   

                ALAND    AWATER  Population     state  \
fips_code                                               
21007       639387454  69473325      7888.0  Kentucky   
21017       750439351   4829777     19788.0  Kentucky   
21031      1103571974  13943044     12879.0  Kentucky   
21065       655509930   6516335     14106.0  Kentucky   
21069       902727151   7182793     14581.0  Kentucky   

                                                    geometry  
fips_code                                                     
21007      POLYGON ((-89.18137 37.04630, -89.17938 37.053...  
21017      POLYGON ((-84.44266 38.28324, -84.44114 38.283...  
21031      POLYGON ((-86.94486 37.07341, -86.94346 37.074...  
21065      POLYGON ((-84.12662 37.64540, -84.12483 37.646...  
21069      POLYGON ((-83.98428 38.44549, -83.98246 38.450...

In [30]:
def find_neighbors(df):
    for index, fips_code in df.iterrows():

        neighbors = df[~df.geometry.disjoint(fips_code.geometry)].index.tolist()
#         neighbors = [int(name) for name in neighbors if name != index]
        print(index, neighbors)
        df.at[index, "NEIGHBORS"] = neighbors
map_data["NEIGHBORS"] = ""
find_neighbors(map_data)

21007 [21007, 17153, 17003, 29133, 21145, 21039]
21017 [21017, 21049, 21097, 21181, 21209, 21011, 21067, 21173]
21031 [21031, 21085, 21183, 21141, 21227, 21061, 21177]
21065 [21065, 21151, 21049, 21109, 21197, 21129]
21069 [21069, 21135, 21181, 21205, 21011, 21201, 21161]
21093 [21093, 21099, 21179, 18061, 21029, 21085, 21027, 21123, 21111, 21163]
21099 [21093, 21099, 21085, 21123, 21169, 21087, 21009, 21061]
21131 [21131, 21193, 21051, 21013, 21095]
21151 [21065, 21151, 21049, 21109, 21079, 21203, 21067, 21113]
21155 [21155, 21179, 21217, 21229, 21123, 21045, 21021]
21179 [21093, 21155, 21179, 21229, 21005, 21029, 21123, 21215]
17091 [17091, 17197, 17075, 17053, 17063, 18111, 17105, 18089]
17187 [17187, 17131, 17057, 17071, 17109, 17095]
17197 [17091, 17197, 17031, 17063, 17043, 18089, 17093]
18027 [18027, 18083, 18125, 18101, 18037, 18055]
18061 [21093, 18061, 18175, 21111, 18043, 21163, 18025]
1001 [1001, 1051, 1101, 1047, 1021, 1085]
1005 [1005, 1113, 13239, 1067, 13259, 13061, 104

37117 [37083, 37117, 37013, 37065, 37015, 37147, 37187]
37127 [37069, 37083, 37127, 37065, 37101, 37183, 37185, 37195]
37165 [37093, 37165, 37153, 45069, 37125, 37155]
37175 [37099, 37175, 45077, 37089, 45073, 37021, 45045, 37087]
37199 [37111, 37199, 37115, 37021, 37121, 47171]
38017 [38017, 38003, 38097, 27107, 38073, 38077, 38091, 27027]
38037 [38037, 38085, 38059, 38089, 38001, 38041]
38085 [38037, 38085, 38059, 38001, 38029, 46031]
38099 [38099, 27089, 38067, 38071, 38035, 38019, 38063]
39035 [39035, 39055, 39103, 39153, 39133, 39085, 39093]
39039 [39039, 39125, 39137, 18003, 39171, 39069, 18033]
39043 [39043, 39077, 39143, 39093]
39125 [39039, 39125, 39137, 18003, 39161]
40065 [40065, 40057, 40075, 40055, 40141, 48487, 48197]
48103 [48103, 48371, 48475, 48135, 48105, 48461]
48141 [48141, 48229, 35013, 35035]
48151 [48151, 48263, 48441, 48353, 48253, 48415, 48433, 48335]
48161 [48161, 48213, 48289, 48001, 48349, 48293]
48167 [48167, 48071, 48039, 48201]
48199 [48199, 48241, 48245,

28149 [28055, 28163, 28149, 22035, 22107, 22065, 28021, 28049]
28151 [28055, 28151, 28011, 28053, 5017, 28133, 28125]
29041 [29033, 29041, 29195, 29117, 29121, 29175, 29115, 29089]
29069 [29143, 29207, 5093, 29023, 29069, 5021, 5055, 5031, 29155]
29087 [29087, 20043, 29005, 31127, 29147, 31147, 29003]
29113 [29113, 29183, 29139, 17013, 29219, 29163]
29159 [29159, 29195, 29107, 29053, 29083, 29141, 29015, 29101]
29183 [29189, 29113, 29183, 17083, 17013, 29219, 17119, 29071]
29195 [29033, 29041, 29159, 29195, 29107, 29053, 29089]
29197 [29199, 29197, 29171, 19007, 29001, 19051]
29201 [29143, 29207, 29031, 29201, 17003, 29133]
30001 [16043, 30023, 30057, 16059, 30001, 30081, 30093, 16033]
30013 [30015, 30013, 30045, 30049, 30059, 30099]
30027 [30015, 30071, 30027, 30045, 30069, 30005, 30037, 30107, 30065]
30031 [16043, 30057, 30031, 30059, 56029, 30043, 30007, 56039, 30067]
30045 [30015, 30013, 30027, 30045, 30059, 30107]
30049 [30029, 30077, 30013, 30049, 30059, 30099, 30043, 30007]
3005

37177 [37095, 37177, 37187]
38005 [38005, 38071, 38103, 38095, 38027, 38069, 38063]
38033 [38033, 38053, 38007, 38087, 30109, 30025]
38053 [30085, 30083, 38033, 38053, 38007, 38061, 38105, 30109, 38025]
38059 [38037, 38085, 38059, 38065, 38089, 38015, 38029, 38057]
38067 [38099, 27089, 38067, 27069, 38019]
38071 [38099, 38005, 38071, 38095, 38019, 38063]
22067 [5003, 22067, 22123, 22111, 5017, 22073, 22083, 5139]
22069 [22031, 22081, 22069, 22079, 22115, 22043, 22127, 22013, 22085]
22079 [22009, 22069, 22079, 22115, 22043, 22003, 22059, 22039]
22097 [22001, 22009, 22099, 22055, 22097, 22077, 22039]
22107 [22029, 28149, 28001, 22107, 22025, 22065, 28021, 22041, 28063]
22113 [22001, 22045, 22053, 22055, 22113, 22023]
22117 [22117, 22105, 28109, 22103, 28091, 28113, 28147]
22123 [22035, 22067, 22123, 5017, 22083]
23007 [23007, 23025, 23011, 23001, 23017]
8065 [8037, 8065, 8093, 8097, 8117, 8015]
8071 [35007, 8023, 8055, 8071, 8101, 8009, 8011, 8089, 35059]
8093 [8019, 8065, 8093, 8043, 81

41015 [41033, 41019, 41015, 41011, 6015]
42049 [36013, 42049, 39007, 42123, 42039]
42101 [34007, 42091, 34005, 34015, 42045, 42101, 42017]
45009 [45005, 45029, 45009, 45011, 45049, 45075]
45057 [45025, 45091, 45055, 45057, 45039, 45023, 37179, 37119]
45087 [45091, 45071, 45059, 45083, 45087, 45021, 45039, 45023]
47025 [47173, 47057, 47013, 47025, 51105, 21235, 21013, 47067]
47053 [47053, 47045, 47183, 47131, 47113, 47017, 47033]
47135 [47005, 47081, 47135, 47085, 47101, 47039, 47181]
47163 [47019, 47073, 47091, 47163, 51191, 51169, 51520, 47179]
48089 [48089, 48015, 48239, 48285, 48481, 48149]
48135 [48103, 48475, 48135, 48461, 48495, 48329, 48003]
48203 [22017, 48315, 48203, 48401, 48459, 48365, 48183]
48323 [48479, 48323, 48507, 48127, 48271, 48463]
48351 [22011, 48241, 48361, 22115, 48351, 48403, 22019, 22085]
48379 [48499, 48467, 48379, 48231, 48223]
48409 [48025, 48007, 48409, 48391, 48355, 48249, 48297]
48465 [48465, 48435, 48271, 48105, 48137, 48443]
49007 [49049, 49047, 49007, 

...

48209 [48055, 48453, 48091, 48187, 48209, 48031]
48233 [48065, 48341, 48421, 48233, 48393, 48195]
48307 [48083, 48411, 48049, 48307, 48095, 48327, 48319]
31173 [31051, 19133, 31039, 31021, 31173, 31179, 31043, 19193]
31175 [31041, 31071, 31077, 31175, 31183, 31163]
35006 [4001, 35003, 35061, 35001, 35006, 35053, 35031, 35043]
35009 [48017, 35037, 48369, 35009, 35041, 48117]
31131 [29005, 31109, 19071, 31067, 31097, 31127, 31131, 31025]
31139 [31167, 31003, 31119, 31139, 31179, 31027, 31107]
48123 [48175, 48469, 48285, 48177, 48123, 48255]
48125 [48263, 48107, 48125, 48269, 48433, 48101, 48153, 48169, 48345]
51680 [51019, 51031, 51680, 51009]
51683 [51153, 51685, 51683]
13005 [13229, 13001, 13069, 13161, 13299, 13005]
13045 [13121, 13149, 13077, 13143, 1029, 13223, 1111, 13045, 13097]
21163 [21093, 18061, 21027, 18123, 21163, 18025]
21191 [21097, 39025, 21191, 21081, 21117, 21037, 21023]
39051 [39095, 39171, 26091, 39069, 39051, 26059]
30065 [30087, 30027, 30069, 30037, 30065, 30111]
35

48363 [48429, 48503, 48143, 48367, 48221, 48133, 48363, 48237]
36041 [36043, 36091, 36031, 36113, 36033, 36041, 36035, 36089]
36093 [36091, 36057, 36095, 36093, 36001]
28077 [28029, 28085, 28091, 28065, 28127, 28147, 28077]
22089 [22057, 22095, 22051, 22089]
22093 [22005, 22057, 22095, 22093, 22007]
20187 [20067, 8009, 20189, 8099, 20093, 20129, 20187, 20075]
23009 [23027, 23019, 23009, 23029]
27049 [27157, 27109, 27131, 55091, 55093, 27049, 27039, 27037]
13129 [13313, 13123, 13213, 13295, 13057, 13015, 13115, 13129, 13227]
29007 [29019, 29027, 29173, 29137, 29139, 29007, 29163, 29175]
42015 [42131, 42117, 42115, 36107, 42081, 42113, 36015, 42015]
46029 [46039, 46051, 46057, 46037, 46029, 46025]
28097 [28007, 28043, 28015, 28019, 28155, 28097]
38009 [38009, 38069, 38079, 38049, 38075]
38011 [46063, 38087, 38001, 38011, 30025]
29215 [29203, 29105, 29067, 29091, 29215, 29229, 29169, 29065, 29161]
29219 [29113, 29183, 29139, 29219, 29073, 29071]
18045 [18121, 18157, 18171, 18165, 18107, 1

47007 [47143, 47035, 47065, 47153, 47007, 47175]
26113 [26055, 26165, 26079, 26133, 26143, 26039, 26035, 26113]
26129 [26135, 26051, 26143, 26001, 26039, 26011, 26069, 26129]
36037 [36029, 36073, 36121, 36051, 36037, 36055, 36063]
50013 [36019, 50007, 50011, 50013]
38073 [38017, 38003, 38045, 38021, 38073, 38081, 38077]
46069 [46085, 46049, 46059, 46107, 46065, 46017, 46069, 46119]
56021 [56031, 8069, 56001, 56015, 31007, 8123, 56021, 31105]
31185 [31151, 31035, 31023, 31081, 31159, 31143, 31185, 31059]
33019 [50027, 50025, 33013, 33005, 33011, 33019, 33009]
19193 [46127, 19035, 19047, 19133, 31173, 19149, 31043, 19093, 19193]
55115 [55067, 55073, 55083, 55135, 55097, 55087, 55115, 55078, 55009]
51035 [51063, 51141, 51155, 51197, 37171, 51035, 51640, 51077]
1031 [1041, 1039, 1061, 1045, 1109, 1031]
1123 [1051, 1087, 1027, 1037, 1017, 1111, 1123, 1081]
35049 [35039, 35033, 35047, 35057, 35001, 35028, 35049, 35043]
47011 [47121, 13313, 13213, 47107, 47065, 47139, 47011]
31107 [46009, 460

17143 [17175, 17179, 17057, 17203, 17123, 17095, 17143]
1079 [1043, 1033, 1103, 1133, 1059, 1077, 1083, 1079]
19069 [19083, 19075, 19079, 19197, 19081, 19023, 19067, 19033, 19069]
16067 [16063, 16013, 16031, 16053, 16067]
42057 [24043, 24001, 42061, 42055, 42009, 42057]
27037 [27053, 27139, 27163, 27131, 27123, 55093, 27049, 27037]
5139 [5011, 5103, 5003, 5013, 22067, 22111, 5027, 22027, 5139]
27051 [27167, 27121, 27041, 27155, 27111, 27149, 27051]
48075 [40057, 48191, 48197, 48087, 48101, 48075]
45031 [45025, 45055, 45069, 45041, 45061, 45031]
17169 [17017, 17125, 17067, 17057, 17009, 17109, 17001, 17169]
17171 [17149, 17137, 17061, 17171]
54091 [54001, 54033, 54049, 54061, 54077, 54091]
13173 [13185, 13019, 13003, 13065, 13101, 13173]
48237 [48503, 48337, 48497, 48009, 48367, 48077, 48363, 48237]
20035 [40113, 20049, 20015, 20173, 40071, 20191, 20019, 20035]
13131 [12039, 12073, 13205, 13087, 13275, 13131]
20155 [20095, 20113, 20173, 20185, 20159, 20151, 20079, 20155]
12117 [12009, 1

1069 [1061, 1067, 13253, 13099, 1045, 12063, 1069]
1121 [1117, 1115, 1015, 1027, 1029, 1037, 1121]
4012 [4013, 6025, 4015, 6071, 4025, 4027, 6065, 4012]
13039 [12089, 13025, 13049, 13127, 13039]
40087 [40027, 40125, 40017, 40123, 40049, 40051, 40087]
27027 [38017, 27167, 27107, 27005, 27111, 38077, 27027]
27113 [27089, 27119, 27125, 27029, 27007, 27113]
29099 [29189, 17133, 29221, 29187, 29186, 29071, 29099]
48117 [48069, 35037, 48369, 48381, 35009, 48375, 48359, 48117]
48147 [40013, 48119, 48277, 48231, 48085, 48181, 48147]
17065 [17059, 17165, 17081, 17191, 17193, 17055, 17065]
45033 [45069, 45067, 45041, 45051, 37155, 45033]
31073 [31137, 31047, 31065, 31063, 31073]
39075 [39151, 39083, 39157, 39169, 39031, 39005, 39075]
48171 [48267, 48299, 48319, 48259, 48265, 48031, 48171]
55079 [55089, 55101, 55133, 55131, 55079]
26139 [26121, 26005, 26081, 26139]


In [54]:
all_data = all_data.reset_index()
all_data["FIPS"] = all_data["GeoFips"]
all_data = all_data.set_index(["TimePeriod","GeoFips"])
all_data.dropna(subset = ["All industry total"], inplace = True)

In [55]:
import datetime

In [56]:
try_df = all_data.reset_index()
try_df.set_index(["GeoFips"])

TimePeriod  Accommodation and food services  \
GeoFips                                                
1001           2001                          46510.0   
1001           2002                          45576.0   
1001           2003                          48870.0   
1001           2004                          49738.0   
1001           2005                          46414.0   
...             ...                              ...   
56045          2016                           3499.0   
56045          2017                              NaN   
56045          2018                              NaN   
56045          2019                              NaN   
56045          2020                              NaN   

         Administrative and support and waste management and remediation services  \
GeoFips                                                                             
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
...                                                    ...                          
56045                                                655.0                          
56045                                                  NaN                          
56045                                                  NaN                          
56045                                                756.0                          
56045                                                908.0                          

         Agriculture, forestry, fishing and hunting  All industry total  \
GeoFips                                                                   
1001                                        22455.0            949800.0   
1001                                        18063.0            984039.0   
1001                                        39941.0           1008032.0   
1001                                        49903.0           1170278.0   
1001                                        59099.0           1195319.0   
...                                             ...                 ...   
56045                                       13871.0            305446.0   
56045                                       19901.0            300909.0   
56045                                       23787.0            315332.0   
56045                                       14194.0            322576.0   
56045                                        8653.0            312665.0   

         Arts, entertainment, and recreation  \
GeoFips                                        
1001                                  2150.0   
1001                                  1935.0   
1001                                  1846.0   
1001                                  1897.0   
1001                                  2277.0   
...                                      ...   
56045                                  351.0   
56045                                    NaN   
56045                                    NaN   
56045                                    NaN   
56045                                    NaN   

         Arts, entertainment, recreation, accommodation, and food services  \
GeoFips                                                                      
1001                                               48577.0                   
1001                                               47411.0                   
1001                                               50585.0                   
1001                                               51503.0                   
1001                                               48623.0                   
...                        

In [57]:
years_list = try_df["TimePeriod"].unique()
all_data["NeighborGDP"] = np.NaN
year_df_dict ={}
for year in years_list:    
    year_data = all_data.loc[year]
    year_data = map_data.join(year_data).dropna(subset = ["All industry total"])
    find_neighbors(year_data)    
#     year_data = year_data.join(map_data["NEIGHBORS"])
#     year_data["NeighborGDP"]
#     print( year_data["All industry total"].loc[year_data.loc[1001]["NEIGHBORS"]].sum())
#     full_df.loc[year, "All industry total"] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
#                           axis = 1)
    all_data["NeighborGDP"].loc[year,year_data.index] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
                          axis = 1)    
    
    
##############################################################################3    
    
    
    year_data["NeighborGDP"] = year_data.apply(
        lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
                              axis = 1)
    year_data["Year"] = datetime.datetime(year,1,1)
    trial = year_data    
    try_df = all_data.reset_index().set_index(["GeoFips"])
    year_df_dict[year] = pd.merge(try_df.loc[try_df["TimePeriod"]==year], trial.loc[trial["Year"].dt.year==year],
                       left_index=True, right_index=True)

21007 [21007, 17153, 17003, 29133, 21145, 21039]
21017 [21017, 21049, 21097, 21181, 21209, 21011, 21067, 21173]
21031 [21031, 21085, 21183, 21141, 21227, 21061, 21177]
21065 [21065, 21151, 21049, 21109, 21197, 21129]
21069 [21069, 21135, 21181, 21205, 21011, 21201, 21161]
21093 [21093, 21099, 21179, 18061, 21029, 21085, 21027, 21123, 21111, 21163]
21099 [21093, 21099, 21085, 21123, 21169, 21087, 21009, 21061]
21131 [21131, 21193, 21051, 21013, 21095]
21151 [21065, 21151, 21049, 21109, 21079, 21203, 21067, 21113]
21155 [21155, 21179, 21217, 21229, 21123, 21045, 21021]
21179 [21093, 21155, 21179, 21229, 21005, 21029, 21123, 21215]
17091 [17091, 17197, 17075, 17053, 17063, 18111, 17105, 18089]
17187 [17187, 17131, 17057, 17071, 17109, 17095]
17197 [17091, 17197, 17031, 17063, 17043, 18089, 17093]
18027 [18027, 18083, 18125, 18101, 18037, 18055]
18061 [21093, 18061, 18175, 21111, 18043, 21163, 18025]
1001 [1001, 1051, 1101, 1047, 1021, 1085]
1005 [1005, 1113, 13239, 1067, 13259, 13061, 104

38017 [38017, 38003, 38097, 27107, 38073, 38077, 38091, 27027]
38037 [38037, 38085, 38059, 38089, 38001, 38041]
38085 [38037, 38085, 38059, 38001, 38029, 46031]
38099 [38099, 27089, 38067, 38071, 38035, 38019, 38063]
39035 [39035, 39055, 39103, 39153, 39133, 39085, 39093]
39039 [39039, 39125, 39137, 18003, 39171, 39069, 18033]
39043 [39043, 39077, 39143, 39093]
39125 [39039, 39125, 39137, 18003, 39161]
40065 [40065, 40057, 40075, 40055, 40141, 48487, 48197]
48103 [48103, 48371, 48475, 48135, 48105, 48461]
48141 [48141, 48229, 35013, 35035]
48151 [48151, 48263, 48441, 48353, 48253, 48415, 48433, 48335]
48161 [48161, 48213, 48289, 48001, 48349, 48293]
48167 [48167, 48071, 48039, 48201]
48199 [48199, 48241, 48245, 48361, 48457, 48373, 48291]
48213 [48161, 48213, 48423, 48467, 48001, 48349, 48139, 48257, 48073]
48229 [48141, 48229, 48109, 48377, 48243, 35035]
48241 [48199, 48241, 48361, 48457, 48005, 48405, 48351, 48403]
48245 [48199, 48245, 48361, 22023, 48291, 48071]
48261 [48261, 48215,

49025 [49025, 4005, 49017, 49037, 49021, 49053, 4015]
5003 [5011, 5003, 22067, 22111, 5017, 5043, 5139]
5007 [5015, 5007, 40041, 29009, 40001, 29119, 5087, 5143]
5013 [5011, 5025, 5103, 5013, 5039, 5139]
5045 [5045, 5029, 5119, 5085, 5145, 5105, 5023, 5141]
13051 [13103, 13051, 13029, 45053]
13077 [13121, 13149, 13077, 13113, 13285, 13255, 13045, 13199]
13123 [13123, 13213, 13111, 13085, 13129, 13227]
13133 [13141, 13133, 13237, 13219, 13265, 13211, 13221]
13137 [13137, 13139, 45073, 13311, 13257, 13011, 13281, 13241]
13139 [13137, 13139, 13157, 13135, 13311, 13117, 13011, 13085, 13187, 13013]
13143 [13143, 1029, 13233, 13223, 13045]
13157 [13139, 13157, 13195, 13219, 13135, 13059, 13011, 13013]
13171 [13171, 13207, 13255, 13035, 13293, 13231]
13181 [13189, 13317, 13181, 45065, 13073, 13105]
13185 [13027, 13185, 12047, 12079, 13075, 13019, 13101, 13173]
13195 [13157, 13195, 13059, 13011, 13119, 13147, 13105, 13221]
13213 [13313, 13123, 13213, 13111, 47139, 13129, 47011]
13217 [13217, 1

51023 [51019, 51023, 51045]
51033 [51085, 51099, 51033, 51057, 51179, 51101, 51097]
51036 [51036, 51041, 51127, 51087, 51181]
51041 [51145, 51007, 51036, 51041, 51087, 51075, 51760]
51057 [51099, 51033, 51057, 51159, 51193, 51119, 51097]
51067 [51019, 51067, 51063, 51141]
51083 [51037, 51083, 37145, 37033, 51117, 37077]
51091 [51017, 51091, 54071, 54075]
51107 [24043, 24021, 24031, 51107, 54037, 51043, 51061]
51111 [51037, 51111, 51147, 51025, 51135, 51117]
51127 [51085, 51036, 51127, 51087, 51101, 51097]
51133 [51133, 51159, 51193, 51103]
51159 [51057, 51133, 51159, 51193, 51103]
51179 [51099, 51033, 51179, 51047, 51061]
51187 [51187, 51157, 51171, 51043, 51139, 51061]
53047 [53007, 53025, 53043, 53047, 53073, 53057, 53019, 53017]
53049 [53049, 53027, 53041, 53069]
53053 [53053, 53077, 53045, 53033, 53067, 53035, 53041]
53061 [53007, 53061, 53033, 53057, 53029]
53071 [53005, 53071, 53021, 41059, 53013]
53073 [53047, 53073, 53057]
54013 [54021, 54087, 54013, 54007, 54085, 54015, 54105]

48287 [48477, 48051, 48287, 48149, 48021, 48331, 48491]
48301 [48475, 35015, 48301, 48389, 35025, 48495]
48311 [48479, 48311, 48283, 48131, 48013, 48297]
48315 [22017, 48067, 48315, 48343, 48203, 48459]
48339 [48471, 48473, 48339, 48407, 48185, 48291, 48201]
48343 [48449, 48037, 48067, 48315, 48343, 48459, 48387, 48063]
48349 [48161, 48213, 48349, 48139, 48217, 48293]
48373 [48199, 48457, 48455, 48005, 48373, 48407, 48291]
48377 [48229, 48043, 48377, 48243]
48383 [48173, 48383, 48451, 48431, 48235, 48105, 48461, 48329]
48405 [48241, 48347, 48005, 48405, 48419, 48403]
48407 [48471, 48455, 48339, 48373, 48407, 48291]
46041 [46117, 46041, 46055, 46107, 46129, 46031, 46119, 46137]
46071 [46095, 46071, 46075, 46055, 46121, 46007, 46103, 46102]
46075 [46095, 46085, 46117, 46071, 46075, 46055]
46079 [46079, 46011, 46077, 46087, 46097, 46099, 46101]
46127 [46127, 31051, 19167, 46027, 19149, 31043, 19193, 46083]
47013 [47001, 47173, 47151, 47013, 47025, 21147, 21235]
47021 [47021, 47037, 47147,

...

2185 [2290, 2188, 2185]
5111 [5067, 5093, 5037, 5031, 5111, 5035]
38015 [38059, 38055, 38065, 38015, 38029, 38043, 38083]
29025 [29033, 29177, 29061, 29025, 29117, 29063, 29049]
29091 [5049, 29203, 29149, 29067, 29091, 29215, 29153]
20191 [20095, 20077, 20015, 40053, 20173, 40071, 20191, 20035]
21039 [21007, 29133, 21083, 21145, 21039, 21105]
48197 [40065, 40057, 48487, 48155, 48197, 48101, 48075]
31067 [31151, 31109, 31095, 31133, 31067, 31097, 31131, 20201, 20117]
31077 [31077, 31093, 31175, 31183, 31125, 31163, 31011]
46065 [46085, 46117, 46065, 46069, 46119]
54051 [42059, 39013, 54069, 54051, 54103, 42125, 39111]
31097 [31109, 31133, 31067, 31097, 31127, 31131]
20145 [20135, 20083, 20009, 20185, 20145, 20047, 20165]
26123 [26133, 26117, 26121, 26123, 26105, 26127, 26107, 26081, 26085]
31127 [29087, 29005, 31133, 31097, 31127, 31131, 31147]
37109 [37023, 37097, 37035, 37109, 37119, 37071, 37045]
37197 [37059, 37193, 37097, 37197, 37171, 37067]
31083 [31137, 31065, 20147, 31083, 2013

12015 [12055, 12071, 12115, 12027, 12051, 12015, 12043]
27017 [27137, 27001, 55031, 27017, 27115]
31163 [31041, 31077, 31093, 31175, 31163, 31019]
29141 [29029, 29159, 29135, 29053, 29131, 29141, 29015]
29145 [29009, 29109, 29119, 20021, 40115, 29097, 29145]
46031 [38085, 46041, 38001, 46129, 38029, 46031, 46137, 46021, 46105]
36039 [36025, 36095, 36021, 36039, 36001, 36083, 36111]
47083 [47005, 47085, 47125, 47161, 47043, 47083]
55133 [55127, 55089, 55101, 55027, 55133, 55055, 55131, 55079]
21009 [21099, 21003, 21171, 21227, 21169, 21009, 21061]
29205 [29137, 29111, 29121, 29205, 29103, 29127]
29211 [29171, 29001, 29079, 29211, 29115, 29129]
48331 [48395, 48051, 48287, 48145, 48331, 48027, 48491]
48363 [48429, 48503, 48143, 48367, 48221, 48133, 48363, 48237]
36041 [36043, 36091, 36031, 36113, 36033, 36041, 36035, 36089]
36093 [36091, 36057, 36095, 36093, 36001]
28077 [28029, 28085, 28091, 28065, 28127, 28147, 28077]
22089 [22057, 22095, 22051, 22089]
22093 [22005, 22057, 22095, 22093,

50013 [36019, 50007, 50011, 50013]
38073 [38017, 38003, 38045, 38021, 38073, 38081, 38077]
46069 [46085, 46049, 46059, 46107, 46065, 46017, 46069, 46119]
56021 [56031, 8069, 56001, 56015, 31007, 8123, 56021, 31105]
31185 [31151, 31035, 31023, 31081, 31159, 31143, 31185, 31059]
33019 [50027, 50025, 33013, 33005, 33011, 33019, 33009]
19193 [46127, 19035, 19047, 19133, 31173, 19149, 31043, 19093, 19193]
55115 [55067, 55073, 55083, 55135, 55097, 55087, 55115, 55078, 55009]
1031 [1041, 1039, 1061, 1045, 1109, 1031]
1123 [1051, 1087, 1027, 1037, 1017, 1111, 1123, 1081]
35049 [35039, 35033, 35047, 35057, 35001, 35028, 35049, 35043]
47011 [47121, 13313, 13213, 47107, 47065, 47139, 47011]
31107 [46009, 46023, 31003, 31089, 31139, 46135, 31027, 31107, 31015]
21233 [21033, 21055, 21101, 21233, 21107, 21149, 21225]
53069 [53015, 53049, 41007, 53041, 41009, 53069]
55095 [27163, 55005, 55033, 27025, 55109, 55095, 55013]
55125 [26053, 55051, 26071, 55085, 55125, 55041, 55099]
41013 [41017, 41023, 410

12117 [12009, 12095, 12127, 12069, 12117]
13013 [13139, 13157, 13219, 13135, 13059, 13297, 13013]
45049 [13103, 45005, 13251, 45029, 45009, 45053, 45049, 45013]
48063 [48499, 48449, 48343, 48459, 48159, 48063]
16077 [16013, 16031, 16071, 16011, 16077, 16005]
49015 [49007, 49019, 49037, 49055, 49041, 49015, 49039]
2105 [2282, 2195, 2100, 2110, 2220, 2105]
22039 [22001, 22009, 22053, 22079, 22097, 22003, 22039]
51097 [51073, 51033, 51057, 51127, 51101, 51119, 51097]
6007 [6115, 6101, 6063, 6011, 6021, 6103, 6007]
13241 [37099, 13137, 37043, 45073, 37113, 13281, 13241]
1025 [1023, 1091, 1131, 1129, 1003, 1099, 1025]
8067 [8083, 35045, 8111, 8033, 8053, 8007, 8067]
13263 [13269, 13215, 13197, 13145, 13053, 13293, 13199, 13263]
21037 [39061, 39025, 21191, 21117, 21037]
16047 [16025, 16039, 16063, 16083, 16053, 16047]
48255 [48025, 48175, 48493, 48177, 48123, 48013, 48297, 48255]
47111 [21003, 47165, 47087, 47169, 21171, 47027, 47111, 47159]
48153 [48045, 48107, 48303, 48189, 48125, 48437, 4

/var/folders/wr/k9fjy7x96svcj5th08wsq71c0000gn/T/ipykernel_42860/3039456499.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_data["NeighborGDP"].loc[year,year_data.index] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan,


In [101]:
# year_df_dict[2020]

In [59]:
df_list = (year_df_dict.values())
#df_list

In [60]:
from functools import reduce

all_data_neigh = pd.concat([d for d in df_list], axis=0, join='inner').set_index(["Year", "FIPS_y"])

In [62]:
unemploy = pd.read_csv('unemployment_rates_by county.csv')

/var/folders/wr/k9fjy7x96svcj5th08wsq71c0000gn/T/ipykernel_42860/3123405110.py:1: DtypeWarning: Columns (3) have mixed types. Specify dtype option on import or set low_memory=False.
  unemploy = pd.read_csv('unemployment_rates_by county.csv')


In [63]:
unemploy = unemploy.rename(columns= {'       value':'unemp'})

In [64]:
# Replace non-numeric values with NaN
unemploy['unemp'] = pd.to_numeric(unemploy['unemp'], errors='coerce')

In [65]:
# Calculate the average value per year for each county
avg_unemp = unemploy.groupby(['year', 'county'])['unemp'].mean().reset_index()

In [66]:
avg_unemp = avg_unemp.rename(columns={'year':'TimePeriod', 'county':'FIPS_y'})

In [67]:
all_data_neigh = pd.merge(all_data_neigh, avg_unemp, on=['TimePeriod', 'FIPS_y'], how='left')

In [68]:
all_data_neigh = all_data_neigh.set_index(['FIPS_y', 'TimePeriod'])

In [69]:
all_data_neigh = all_data_neigh.sort_index()

In [73]:
ai_data_nominal = all_data_neigh.sort_index()
ai_data_nominal
key = ['Agriculture, forestry, fishing and hunting_y',
 'Mining, quarrying, and oil and gas extraction_y',
 'Utilities_y',
 "All industry total_y", 'M4_y', 'M4 Interest Rate_y', 'NeighborGDP_y', 'unemp']
ai_data_nominal = ai_data_nominal[key]

Nominal gdp including m4 variables, neighbor gdp and unemployment

In [76]:
ai_data_nominal.to_csv('nominal_data.csv', index=True) 

## Data work on Real GDP

In [80]:
all_data1 = full_df.copy()

In [82]:
all_data1 = all_data1.reset_index()

In [84]:
cpi = cpi.reset_index()

In [87]:
# Iterate over unique combinations of county and year
for index, row in all_data1.iterrows():
    county = row['GeoFips']
    year = row['TimePeriod']
    
    # Check if the CPI dataframe is not empty and contains the year
    if not cpi.empty and year in cpi['TimePeriod'].values:
        cpi_value = cpi[cpi['TimePeriod'] == year]['CPIAUCSL_PCA'].values[0]
        
        # Convert the CPI value to a numeric type
        cpi_value = pd.to_numeric(cpi_value, errors='coerce')
        
        # Divide all variables by the CPI value
        for col in all_data1.columns[2:]:  # Assuming columns from 'var1' onwards contain the variables
            all_data1.loc[index, col] /= cpi_value
    else:
        # Handle the case where the CPI data is missing or the year is not found
        print(f"CPI data not available for year {year}. Skipping division for index {index}.")


In [90]:
cpi = cpi.set_index('TimePeriod')

In [94]:
all_data1 = all_data1.copy().reset_index().set_index("TimePeriod")
all_data1 = all_data1.join(divisia).reset_index()     
all_data1 = all_data1.set_index(["GeoFips", "TimePeriod"])    
all_data1 = all_data1.sort_index()


ValueError: columns overlap but no suffix specified: Index(['M4', 'M4 Interest Rate', 'RM4Interest Rate', 'RM4'], dtype='object')

In [95]:
all_data1

GeoFips  index  Accommodation and food services  \
TimePeriod                                                    
2001           1001      0                     16512.640993   
2002           1001      1                     28562.296715   
2003           1001      2                     21266.318538   
2004           1001      3                     18645.433859   
2005           1001      4                     13789.763595   
...             ...    ...                              ...   
2016          56045  62355                      2760.857215   
2017          56045  62356                              NaN   
2018          56045  62357                              NaN   
2019          56045  62358                              NaN   
2020          56045  62359                              NaN   

            Administrative and support and waste management and remediation services  \
TimePeriod                                                                             
2001                                                      NaN                          
2002                                                      NaN                          
2003                                                      NaN                          
2004                                                      NaN                          
2005                                                      NaN                          
...                                                       ...                          
2016                                               516.822371                          
2017                                                      NaN                          
2018                                                      NaN                          
2019                                               416.928626                          
2020                                               726.871012                          

            Agriculture, forestry, fishing and hunting  All industry total  \
TimePeriod                                                                   
2001                                       7972.293130       337211.490327   
2002                                      11320.009776       616693.301246   
2003                                      17380.765883       438656.222802   
2004                                      18707.287906       438705.638465   
2005                                      17558.521969       355133.503475   
...                                                ...                 ...   
2016                                      10944.798637       241009.657871   
2017                                       9336.880231       141176.387794   
2018                                       9752.767528       129287.412874   
2019                                       7827.890098       177898.370890   
2020                                       6926.888624       250294.190636   

            Arts, entertainment, and recreation  \
TimePeriod                                        
2001                                 763.323546   
2002                                1212.656752   
2003                                 803.307224   
2004                                 711.134103   
2005                                 676.504755   
...                                         ...   
2016                                 276.953667   
2017                                        NaN   
2018                                        NaN   
2019                                        NaN   
2020                                        NaN   

            Arts, entertainment, recreation, accommodation, and food services  \
TimePeriod                                                                      
2001                                             17246.496700                   
2002                                             29712.283868                   
2003                                        

In [96]:
all_data1 = all_data1.reset_index()
all_data1["FIPS"] = all_data1["GeoFips"]
all_data1 = all_data1.set_index(["TimePeriod","GeoFips"])
all_data1.dropna(subset = ["All industry total"], inplace = True)

In [99]:
try_df1 = all_data1.reset_index()
try_df1.set_index(["GeoFips"])

TimePeriod  index  Accommodation and food services  \
GeoFips                                                       
1001           2001      0                     16512.640993   
1001           2002      1                     28562.296715   
1001           2003      2                     21266.318538   
1001           2004      3                     18645.433859   
1001           2005      4                     13789.763595   
...             ...    ...                              ...   
56045          2016  62355                      2760.857215   
56045          2017  62356                              NaN   
56045          2018  62357                              NaN   
56045          2019  62358                              NaN   
56045          2020  62359                              NaN   

         Administrative and support and waste management and remediation services  \
GeoFips                                                                             
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
1001                                                   NaN                          
...                                                    ...                          
56045                                           516.822371                          
56045                                                  NaN                          
56045                                                  NaN                          
56045                                           416.928626                          
56045                                           726.871012                          

         Agriculture, forestry, fishing and hunting  All industry total  \
GeoFips                                                                   
1001                                    7972.293130       337211.490327   
1001                                   11320.009776       616693.301246   
1001                                   17380.765883       438656.222802   
1001                                   18707.287906       438705.638465   
1001                                   17558.521969       355133.503475   
...                                             ...                 ...   
56045                                  10944.798637       241009.657871   
56045                                   9336.880231       141176.387794   
56045                                   9752.767528       129287.412874   
56045                                   7827.890098       177898.370890   
56045                                   6926.888624       250294.190636   

         Arts, entertainment, and recreation  \
GeoFips                                        
1001                              763.323546   
1001                             1212.656752   
1001                              803.307224   
1001                              711.134103   
1001                              676.504755   
...                                      ...   
56045                             276.953667   
56045                                    NaN   
56045                                    NaN   
56045                                    NaN   
56045                                    NaN   

         Arts, entertainment, recreation, accommodation, and food services  \
GeoFips                                                                      
1001                                          17246.496700                   
1001                                          29712.283868                   
1001                                          22012.619669                   
1001                                          19307.084725                   
1001          

In [100]:
years_list = try_df1["TimePeriod"].unique()
all_data1["NeighborGDP"] = np.NaN
year_df_dict ={}
for year in years_list:    
    year_data = all_data1.loc[year]
    year_data = map_data.join(year_data).dropna(subset = ["All industry total"])
    find_neighbors(year_data)    
#     year_data = year_data.join(map_data["NEIGHBORS"])
#     year_data["NeighborGDP"]
#     print( year_data["All industry total"].loc[year_data.loc[1001]["NEIGHBORS"]].sum())
#     full_df.loc[year, "All industry total"] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
#                           axis = 1)
    all_data1["NeighborGDP"].loc[year,year_data.index] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
                          axis = 1)    
    
    
##############################################################################3    
    
    
    year_data["NeighborGDP"] = year_data.apply(
        lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan, 
                              axis = 1)
    year_data["Year"] = datetime.datetime(year,1,1)
    trial = year_data    
    try_df1 = all_data1.reset_index().set_index(["GeoFips"])
    year_df_dict[year] = pd.merge(try_df1.loc[try_df1["TimePeriod"]==year], trial.loc[trial["Year"].dt.year==year],
                       left_index=True, right_index=True)

21007 [21007, 17153, 17003, 29133, 21145, 21039]
21017 [21017, 21049, 21097, 21181, 21209, 21011, 21067, 21173]
21031 [21031, 21085, 21183, 21141, 21227, 21061, 21177]
21065 [21065, 21151, 21049, 21109, 21197, 21129]
21069 [21069, 21135, 21181, 21205, 21011, 21201, 21161]
21093 [21093, 21099, 21179, 18061, 21029, 21085, 21027, 21123, 21111, 21163]
21099 [21093, 21099, 21085, 21123, 21169, 21087, 21009, 21061]
21131 [21131, 21193, 21051, 21013, 21095]
21151 [21065, 21151, 21049, 21109, 21079, 21203, 21067, 21113]
21155 [21155, 21179, 21217, 21229, 21123, 21045, 21021]
21179 [21093, 21155, 21179, 21229, 21005, 21029, 21123, 21215]
17091 [17091, 17197, 17075, 17053, 17063, 18111, 17105, 18089]
17187 [17187, 17131, 17057, 17071, 17109, 17095]
17197 [17091, 17197, 17031, 17063, 17043, 18089, 17093]
18027 [18027, 18083, 18125, 18101, 18037, 18055]
18061 [21093, 18061, 18175, 21111, 18043, 21163, 18025]
1001 [1001, 1051, 1101, 1047, 1021, 1085]
1005 [1005, 1113, 13239, 1067, 13259, 13061, 104

38017 [38017, 38003, 38097, 27107, 38073, 38077, 38091, 27027]
38037 [38037, 38085, 38059, 38089, 38001, 38041]
38085 [38037, 38085, 38059, 38001, 38029, 46031]
38099 [38099, 27089, 38067, 38071, 38035, 38019, 38063]
39035 [39035, 39055, 39103, 39153, 39133, 39085, 39093]
39039 [39039, 39125, 39137, 18003, 39171, 39069, 18033]
39043 [39043, 39077, 39143, 39093]
39125 [39039, 39125, 39137, 18003, 39161]
40065 [40065, 40057, 40075, 40055, 40141, 48487, 48197]
48103 [48103, 48371, 48475, 48135, 48105, 48461]
48141 [48141, 48229, 35013, 35035]
48151 [48151, 48263, 48441, 48353, 48253, 48415, 48433, 48335]
48161 [48161, 48213, 48289, 48001, 48349, 48293]
48167 [48167, 48071, 48039, 48201]
48199 [48199, 48241, 48245, 48361, 48457, 48373, 48291]
48213 [48161, 48213, 48423, 48467, 48001, 48349, 48139, 48257, 48073]
48229 [48141, 48229, 48109, 48377, 48243, 35035]
48241 [48199, 48241, 48361, 48457, 48005, 48405, 48351, 48403]
48245 [48199, 48245, 48361, 22023, 48291, 48071]
48261 [48261, 48215,

5045 [5045, 5029, 5119, 5085, 5145, 5105, 5023, 5141]
13051 [13103, 13051, 13029, 45053]
13077 [13121, 13149, 13077, 13113, 13285, 13255, 13045, 13199]
13123 [13123, 13213, 13111, 13085, 13129, 13227]
13133 [13141, 13133, 13237, 13219, 13265, 13211, 13221]
13137 [13137, 13139, 45073, 13311, 13257, 13011, 13281, 13241]
13139 [13137, 13139, 13157, 13135, 13311, 13117, 13011, 13085, 13187, 13013]
13143 [13143, 1029, 13233, 13223, 13045]
13157 [13139, 13157, 13195, 13219, 13135, 13059, 13011, 13013]
13171 [13171, 13207, 13255, 13035, 13293, 13231]
13181 [13189, 13317, 13181, 45065, 13073, 13105]
13185 [13027, 13185, 12047, 12079, 13075, 13019, 13101, 13173]
13195 [13157, 13195, 13059, 13011, 13119, 13147, 13105, 13221]
13213 [13313, 13123, 13213, 13111, 47139, 13129, 47011]
13217 [13217, 13151, 13159, 13035, 13211, 13247, 13297]
13237 [13009, 13141, 13133, 13237, 13159, 13169, 13211]
13245 [13189, 13245, 45003, 13073, 45037, 13033, 13163]
13251 [13103, 45005, 13251, 13031, 13165, 13033, 45

51033 [51085, 51099, 51033, 51057, 51179, 51101, 51097]
51036 [51036, 51041, 51127, 51087, 51181]
51041 [51145, 51007, 51036, 51041, 51087, 51075, 51760]
51057 [51099, 51033, 51057, 51159, 51193, 51119, 51097]
51067 [51019, 51067, 51063, 51141]
51083 [51037, 51083, 37145, 37033, 51117, 37077]
51091 [51017, 51091, 54071, 54075]
51107 [24043, 24021, 24031, 51107, 54037, 51043, 51061]
51111 [51037, 51111, 51147, 51025, 51135, 51117]
51127 [51085, 51036, 51127, 51087, 51101, 51097]
51133 [51133, 51159, 51193, 51103]
51159 [51057, 51133, 51159, 51193, 51103]
51179 [51099, 51033, 51179, 51047, 51061]
51187 [51187, 51157, 51171, 51043, 51139, 51061]
53047 [53007, 53025, 53043, 53047, 53073, 53057, 53019, 53017]
53049 [53049, 53027, 53041, 53069]
53053 [53053, 53077, 53045, 53033, 53067, 53035, 53041]
53061 [53007, 53061, 53033, 53057, 53029]
53071 [53005, 53071, 53021, 41059, 53013]
53073 [53047, 53073, 53057]
54013 [54021, 54087, 54013, 54007, 54085, 54015, 54105]
54017 [54021, 54017, 54033,

48315 [22017, 48067, 48315, 48343, 48203, 48459]
48339 [48471, 48473, 48339, 48407, 48185, 48291, 48201]
48343 [48449, 48037, 48067, 48315, 48343, 48459, 48387, 48063]
48349 [48161, 48213, 48349, 48139, 48217, 48293]
48373 [48199, 48457, 48455, 48005, 48373, 48407, 48291]
48377 [48229, 48043, 48377, 48243]
48383 [48173, 48383, 48451, 48431, 48235, 48105, 48461, 48329]
48405 [48241, 48347, 48005, 48405, 48419, 48403]
48407 [48471, 48455, 48339, 48373, 48407, 48291]
46041 [46117, 46041, 46055, 46107, 46129, 46031, 46119, 46137]
46071 [46095, 46071, 46075, 46055, 46121, 46007, 46103, 46102]
46075 [46095, 46085, 46117, 46071, 46075, 46055]
46079 [46079, 46011, 46077, 46087, 46097, 46099, 46101]
46127 [46127, 31051, 19167, 46027, 19149, 31043, 19193, 46083]
47013 [47001, 47173, 47151, 47013, 47025, 21147, 21235]
47021 [47021, 47037, 47147, 47125, 47043, 47187]
47031 [47003, 47149, 47031, 47127, 47177, 47061, 47051, 47015]
47035 [47049, 47143, 47185, 47035, 47129, 47145, 47007, 47141, 47175]

...

20205 [20049, 20073, 20001, 20125, 20205, 20133, 20207]
48447 [48429, 48503, 48275, 48009, 48417, 48447, 48023, 48207]
29139 [29113, 29027, 29151, 29139, 29007, 29219, 29073, 29163]
47103 [1089, 47003, 47117, 47127, 47055, 1083, 47103, 47051]
31121 [31081, 31141, 31093, 31121, 31125, 31143, 31079]
31125 [31141, 31077, 31093, 31121, 31125, 31011]
46135 [46067, 46009, 46125, 46027, 46135, 31027, 31107]
5127 [40079, 5149, 5113, 5083, 5127, 5097, 5131]
13199 [13077, 13145, 13285, 13255, 13293, 13199, 13231, 13263]
21211 [21005, 21103, 21111, 21215, 21073, 21211, 21185]
40091 [40101, 40107, 40121, 40061, 40111, 40091, 40063]
19037 [19017, 19131, 19191, 19089, 19023, 19067, 19037, 19065]
55141 [55001, 55057, 55073, 55097, 55141, 55019, 55053]
30079 [30055, 30033, 30109, 30017, 30021, 30079, 30025]
38019 [38099, 38067, 38071, 38095, 38019]
38021 [38045, 38051, 46089, 38021, 46013, 38073, 38081]
47027 [47087, 21171, 47133, 47027, 21053, 47137, 47111, 21057]
47047 [47157, 47167, 47075, 47069, 4

23029 [23003, 23019, 23009, 23029]
50023 [50017, 50007, 50015, 50023, 50001, 50005]
1127 [1043, 1009, 1073, 1093, 1133, 1057, 1125, 1127]
2164 [2050, 2070, 2150, 2060, 2013, 2122, 2164]
29059 [29029, 29167, 29085, 29105, 29077, 29225, 29059]
29063 [29021, 29061, 29075, 29025, 29063, 29049, 29003]
36007 [36025, 42127, 36017, 42115, 36107, 36023, 36007]
28131 [28109, 28047, 28059, 28039, 28035, 28111, 28045, 28131]
29049 [29021, 29177, 29047, 29165, 29025, 29063, 29049]
48099 [48035, 48309, 48281, 48027, 48193, 48099]
22027 [22119, 22111, 5027, 22027, 5139, 22061, 22013]
24037 [24017, 24009, 24037]
26047 [26031, 26029, 26047]
29217 [29013, 29011, 20037, 29039, 29185, 20011, 29217, 20107]
4019 [4009, 4013, 4023, 4021, 4003, 4019, 4027]
56043 [56029, 56003, 56013, 56019, 56017, 56043, 56025]
20005 [20085, 20043, 20087, 29021, 20013, 29165, 20005, 20103]
46013 [46049, 46089, 46045, 46091, 46115, 46037, 38021, 46013, 38081]
46017 [46073, 46085, 46015, 46059, 46017, 46069]
31049 [31033, 8115,

47059 [47029, 47063, 47073, 37115, 47179, 47171, 47059]
1099 [1035, 1131, 1013, 1053, 1003, 1099, 1025]
42129 [42005, 42111, 42003, 42051, 42063, 42021, 42129, 42125]
48003 [48317, 48135, 48165, 35025, 48495, 48329, 48003]
48265 [48385, 48267, 48137, 48019, 48259, 48265, 48171]
48293 [48161, 48289, 48395, 48349, 48309, 48145, 48217, 48293]
48437 [48011, 48045, 48069, 48381, 48189, 48437, 48153]
6067 [6005, 6013, 6101, 6113, 6095, 6077, 6061, 6017, 6067]
17143 [17175, 17179, 17057, 17203, 17123, 17095, 17143]
1079 [1043, 1033, 1103, 1133, 1059, 1077, 1083, 1079]
19069 [19083, 19075, 19079, 19197, 19081, 19023, 19067, 19033, 19069]
16067 [16063, 16013, 16031, 16053, 16067]
42057 [24043, 24001, 42061, 42055, 42009, 42057]
27037 [27053, 27139, 27163, 27131, 27123, 55093, 27049, 27037]
5139 [5011, 5103, 5003, 5013, 22067, 22111, 5027, 22027, 5139]
27051 [27167, 27121, 27041, 27155, 27111, 27149, 27051]
48075 [40057, 48191, 48197, 48087, 48101, 48075]
45031 [45025, 45055, 45069, 45041, 45061

5131 [40079, 40135, 5083, 5047, 5127, 5033, 5131]
6065 [6059, 6073, 6025, 6071, 6065, 4012]
1069 [1061, 1067, 13253, 13099, 1045, 12063, 1069]
1121 [1117, 1115, 1015, 1027, 1029, 1037, 1121]
4012 [4013, 6025, 4015, 6071, 4025, 4027, 6065, 4012]
13039 [12089, 13025, 13049, 13127, 13039]
40087 [40027, 40125, 40017, 40123, 40049, 40051, 40087]
27027 [38017, 27167, 27107, 27005, 27111, 38077, 27027]
27113 [27089, 27119, 27125, 27029, 27007, 27113]
29099 [29189, 17133, 29221, 29187, 29186, 29071, 29099]
48117 [48069, 35037, 48369, 48381, 35009, 48375, 48359, 48117]
48147 [40013, 48119, 48277, 48231, 48085, 48181, 48147]
17065 [17059, 17165, 17081, 17191, 17193, 17055, 17065]
45033 [45069, 45067, 45041, 45051, 37155, 45033]
31073 [31137, 31047, 31065, 31063, 31073]
39075 [39151, 39083, 39157, 39169, 39031, 39005, 39075]
48171 [48267, 48299, 48319, 48259, 48265, 48031, 48171]
55079 [55089, 55101, 55133, 55131, 55079]
26139 [26121, 26005, 26081, 26139]


/var/folders/wr/k9fjy7x96svcj5th08wsq71c0000gn/T/ipykernel_42860/262081964.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_data1["NeighborGDP"].loc[year,year_data.index] = year_data.apply(lambda row: year_data["All industry total"].loc[row["NEIGHBORS"]].sum() if row["NEIGHBORS"] != np.nan else np.nan,


In [102]:
df_list = (year_df_dict.values())
#df_list

In [103]:
from functools import reduce

all_data1_neigh = pd.concat([d for d in df_list], axis=0, join='inner').set_index(["Year", "FIPS_y"])

In [104]:
all_data1_neigh = pd.merge(all_data1_neigh, avg_unemp, on=['TimePeriod', 'FIPS_y'], how='left')

In [105]:
all_data1_neigh = all_data1_neigh.set_index(['FIPS_y', 'TimePeriod'])

In [106]:
all_data1_neigh = all_data1_neigh.sort_index()

In [108]:
all_data1_neigh.columns

Index(['index_x', 'Accommodation and food services_x',
       'Administrative and support and waste management and remediation services_x',
       'Agriculture, forestry, fishing and hunting_x', 'All industry total_x',
       'Arts, entertainment, and recreation_x',
       'Arts, entertainment, recreation, accommodation, and food services_x',
       'Construction_x', 'Durable goods manufacturing_x',
       'Educational services, health care, and social assistance_x',
       'Educational services_x', 'Finance and insurance_x',
       'Finance, insurance, real estate, rental, and leasing_x',
       'Government and government enterprises_x',
       'Health care and social assistance_x', 'Information_x',
       'Management of companies and enterprises_x',
       'Manufacturing and information_x', 'Manufacturing_x',
       'Mining, quarrying, and oil and gas extraction_x',
       'Natural resources and mining_x', 'Nondurable goods manufacturing_x',
       'Other services (except government 

In [109]:
ai_data_real = all_data1_neigh.sort_index()
ai_data_real
key = ['Agriculture, forestry, fishing and hunting_y',
 'Mining, quarrying, and oil and gas extraction_y',
 'Utilities_y',
 "All industry total_y", 'RM4_y', 'RM4Interest Rate_y', 'NeighborGDP_y', 'unemp']
ai_data_real = ai_data_real[key]

In [112]:
ai_data_nominal.rename(columns = {key:key[:4].replace("\n", "") for key in ai_data_nominal.keys()}, inplace = True)
list(ai_data_nominal.keys())

['Agri', 'Mini', 'Util', 'All ', 'M4_y', 'M4 I', 'Neig', 'unem']

In [113]:
ai_data_real.rename(columns = {key:key[:4].replace("\n", "") for key in ai_data_real.keys()}, inplace = True)
list(ai_data_real.keys())

['Agri', 'Mini', 'Util', 'All ', 'RM4_', 'RM4I', 'Neig', 'unem']

In [118]:
ai_data_nominal.to_csv('nominal_data.csv', index=True)

In [119]:
ai_data_real.to_csv('real_data.csv', index=True) 